## Numerical Evaluation of Distributions in Random Matrix Theorm
Boya Song (boyasong@mit.edu)

2nd year PhD student in physical applied math 

This project is baed on the two papers 'MarkovProcRelFields16.pdf' and 'MathComp79.pdf‘ that are included in the email. For people who will actually use this code, please read the section "Potential improvement" at the bottom of this document. PLease feel free to contact me about any question of this code.    


In [28]:
include("NumericalRMT.jl")

Airy2ProcessKernel (generic function with 1 method)

### 9.1.4: Compute Fredholm Determinant

For a lienar integral operator $\mathcal{L}[u] = \int_b^a K(x,y) u(y) d y$ asociated with a kernel function $K(x,y)$, the Fredholm determinant is defined as  $d(z) = \det \left(I-z\mathcal{L}[u] \right) = \det \left(I-z \int_b^a K(x,y) u(y) d y\right)$.

In [2]:
# 9.4.1
m=64;
a=0; b=Inf;
z = 1; 

ops = FDoptions([a,b],m,1e-14,z);

(rst, err) = FredholmDet(airy,ops);
PrintCorrectDigits(rst, err)

(rst, err) = FredholmDet(AiryKernel,ops);
PrintCorrectDigits(rst, err)

0.83190806620294__
0.96937282835526__


In [3]:
dump(ops)

FDoptions
  J: Array{Real}((2,)) Real[0.0, Inf]
  m: Int64 64
  tol: Float64 1.0e-14
  z: Int64 1
  max_m: Int64 256


### Example 9.2.2

In [4]:
s = -1.23456789; 
z = -3.1415926535 + 2.7182818284im;

ops = FDoptions([s, Inf]);
ops.m=16;
ops.tol = 1e-4;
ops.max_m = 32;

# Equivalently for  matrix kernel,
# J = fill(Array{Real,1}([s, Inf]),(2,2))
# ops2 = FDoptions(J);

# f11(x,y) =F4MatrixKernel(x,y,64,"SN");
# f12(x,y) =F4MatrixKernel(x,y,64,"SD");
# f21(x,y) =F4MatrixKernel(x,y,64,"IS");
# f22(x,y) =F4MatrixKernel(x,y,64,"ST");
# F4Mat = [f11 f12; f21 f22];
F4Mat = F4Matrix(m)

ans1 = sqrt(FredholmDet(F4Mat, z, ops, returnErr = false));
ans2 = (FredholmDet(airy, sqrt(z), ops, returnErr = false) +
    FredholmDet(airy, -sqrt(z), ops, returnErr = false))/2 ;
println(ans1)
println(ans2)
println(abs(ans1 - ans2))

1.0863088370559744 - 0.07468117484054973im
1.0862991632143528 - 0.07467121693054718im
1.3883197878640778e-5


Reach maximal number of 32 discritization points.


### Example  9.3.1

In [5]:
val,err = F(1,0);
PrintCorrectDigits(val,err);

println()

val,err = F(2,0);
PrintCorrectDigits(val,err);

0.83190806620294__

0.96937282835526__


### Example  9.3.2

In [6]:
s = 0; beta = 2;
mass = 0; errmass = 0; mean = 0; errmean = 0;
M = 3; 
for k=0:M
    val,err = E(beta,k,s,"soft");
    mass = mass+val; errmass = errmass+err;
    mean = mean+k*val; errmean = errmean+k*err;
end
PrintCorrectDigits(mass,errmass)
PrintCorrectDigits(mean,errmean)
1/9/gamma(1/3)/gamma(2/3)

1.00000000000001__
0.0306293830790____


0.03062938307898844

### Example A.1.1

In [30]:
s = 6;
# a strong singularity; 
# cannot be resolved by current version of the code
# need a different quadrature rule 
alpha = -0.5; 
kOps = FDoptions([0, s]);
val1,err1 = dzdet((x,y)->BesselKernel(alpha,x,y),1, kOps);
PrintCorrectDigits(val1 ,err1);
# a weaker singularity
alpha = 0.5; 
val,err = dzdet((x,y)->BesselKernel(alpha,x,y),1, kOps);
PrintCorrectDigits(val ,err);

_________________


0.524976__________


In [8]:
(val1, err1)

(227.7420273135761, 687.8099424769416)

### An example in Page 47

In [29]:
val1,err1 = E("+",1,2*sqrt(s)/pi);
val2,err2 = E("-",1,2*sqrt(s)/pi);
PrintCorrectDigits(val1, err1);
PrintCorrectDigits(val2,err2);

0.86114217058328_
0.524976779218593_


### Some extra comparasion with the MATLAB toolbox

In [10]:
ops = FDoptions([0,1]);
ops.m = 8;
ops.tol = 1e-10;
(val,err) = dzdet(sinc, 3, ops) # 0.001862683691592

(0.001862683691592211, 2.1163626406917047e-16)

In [11]:
ops = FDoptions([-1, Inf]);
ops.m = 8;
ops.tol = 1e-10;
r = 0.5
func(x,y) = real(my_airyai((x+y)/2))/2
dzdet(func,3,ops,sqrt, ops, r) #0.024971590789817

(0.024971590789817144, 4.163336342344337e-16)

In [12]:
f11(x,y) =AiryKernel(x,y);
f12(x,y) =AiryKernel(x,y);
f21(x,y) =AiryKernel(x,y);
f22(x,y) =AiryKernel(x,y);
FMat = [f11 f12; f21 f22];
J = fill(Array{Real,1}([1, Inf]),(2,2))
J[1, 1] = Array{Real, 1}([0,1]);
J[2, 1] = Array{Real, 1}([0,1]);
#J = fill(Array{Real,1}([1, Inf]),2)
#J[2] = Array{Real, 1}([0,1]);
ops = FDoptions(J)
ops.m = 8;
ops.tol = 1e-10;
dzdet(FMat,[1, 0],ops, identity, ops, 0.1) #0.028131578038884

(0.028132143299108126 + 0.0im, 1.157262252693414e-7)

In [13]:
ops = FDoptions([-6, Inf])
ops.m = 16;
ops.tol = 1e-4;
dzsqrtdet(F4Matrix(64),2,ops) # 0.416935212291463

(0.41692026802590476, 8.42793248949647e-5)

## Things that are constrained in Julia
- `airyai(1e7)` and `airyai(-1e7)`
- <strike>`log(abs(gamma))` is not accurate (comparing with `gammaln` in MATLAB)</strike> 'lgamma' does the job
- (just a little bit annoying) default field values (as in https://github.com/JuliaLang/julia/issues/10146)
- `ApproxFun` is noticablely slow when doing some integrations (e.g. integrate airyai(x))


## Potential improvement:
The code should use other quaterature rule if needed; current quaterature rule sometimes give really bad quaterature result on materix kernels, therefore in this package the `E2` function with kernel matrix is implemented but commentted out (it doesn't fail all the cases, but sometimes the error could be really large). For this reason `f2joint` is also commented out. All the functions are included at the bottom of `NumericalRMT.jl` for people who want to improve on it.


